In [2]:
# Imports
import pandas as pd
import numpy as np
from pathlib import Path
import hvplot.pandas as hv
import matplotlib.pyplot as plt
from sklearn import svm
from sklearn.svm import SVC
from sklearn.preprocessing import StandardScaler
from pandas.tseries.offsets import DateOffset
from sklearn.metrics import classification_report
import datetime as dt
from finta import TA
%matplotlib inline

pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 500)
pd.set_option('display.width', 300)

from sklearn.linear_model import LogisticRegression

In [35]:
# Import the CSV dataset into a Pandas Dataframe
Path="../Resources/Data/Bay-Area_zhvf_uc_sfrcondo_tier_0.33_0.67_sm_sa_mon.csv"
sfzhvf_df = pd.read_csv(Path)

# Review the DataFrame
sfzhvf_df.head(25)

Region  RegionName StateName          CountyName        CityName ForecastedDate  ForecastYoYPctChange
0     Zip       94002        CA    San Mateo County         Belmont      2/28/2022                   3.2
1     Zip       94005        CA    San Mateo County        Brisbane      2/28/2022                   3.8
2     Zip       94010        CA    San Mateo County      Burlingame      2/28/2022                   2.8
3     Zip       94014        CA    San Mateo County       Daly City      2/28/2022                   1.9
4     Zip       94015        CA    San Mateo County       Daly City      2/28/2022                   3.2
5     Zip       94018        CA    San Mateo County   Half Moon Bay      2/28/2022                   3.8
6     Zip       94019        CA    San Mateo County   Half Moon Bay      2/28/2022                   2.8
7     Zip       94020        CA    San Mateo County        La Honda      2/28/2022                   1.5
8     Zip       94021        CA    San Mateo County       Pescadero      2/28/2022                   4.8
9     Zip       94022        CA  Santa Clara County       Los Altos      2/28/2022                   3.7
10    Zip       94024        CA  Santa Clara County       Los Altos      2/28/2022                   3.9
11    Zip       94025        CA    San Mateo County      Menlo Park      2/28/2022                   2.8
12    Zip       94027        CA    San Mateo County        Atherton      2/28/2022                   2.6
13    Zip       94028        CA    San Mateo County  Portola Valley      2/28/2022                   2.2
14    Zip       94030        CA    San Mateo County        Millbrae      2/28/2022                   1.2
15    Zip       94037        CA    San Mateo County         Montara      2/28/2022                   3.4
16    Zip       94038        CA    San Mateo County      Moss Beach      2/28/2022                   3.3
17    Zip       94040        CA  Santa Clara County   Mountain View      2/28/2022                   3.4
18    Zip       94041        CA  Santa Clara County   Mountain View      2/28/2022                   3.4
19    Zip       94043        CA  Santa Clara County   Mountain View      2/28/2022                   2.4
20    Zip       94044        CA    San Mateo County        Pacifica      2/28/2022                   3.5
21    Zip       94060        CA    San Mateo County       Pescadero      2/28/2022                   3.2
22    Zip       94061        CA    San Mateo County    Redwood City      2/28/2022                   2.8
23    Zip       94062        CA    San Mateo County    Redwood City      2/28/2022                   3.7
24    Zip       94063        CA    San Mateo County    Redwood City      2/28/2022                   3.1

In [5]:
# Import the CSV dataset into a Pandas Dataframe
sfzhvi_df = pd.read_csv(
    Path("../Resources/Data/Bay-Area_Zip_zhvi_uc_sfrcondo_tier_0.33_0.67_sm_sa_mon.csv"),
    
)

# Review the DataFrame
sfzhvi_df.head(25)

RegionID  SizeRank  RegionName RegionType StateName State                 City                           Metro            CountyName  1/31/1996  2/29/1996  3/31/1996  4/30/1996  5/31/1996  6/30/1996  7/31/1996  8/31/1996  9/30/1996  10/31/1996  11/30/1996  12/31/1996  1/31/1997  2/28/1997  \
0      97564        13       94109        Zip        CA    CA        San Francisco   San Francisco-Oakland-Hayward  San Francisco County   333727.0   332205.0   331788.0   330713.0   330535.0   330277.0   330447.0   331116.0   332377.0    333532.0    335011.0    336512.0   339376.0   342975.0   
1      97771        40       94565        Zip        CA    CA            Pittsburg   San Francisco-Oakland-Hayward   Contra Costa County        NaN        NaN        NaN        NaN        NaN        NaN        NaN        NaN        NaN         NaN         NaN         NaN        NaN        NaN   
2      97711        88       94501        Zip        CA    CA              Alameda   San Francisco-Oakland-Hayward        Alameda County   183651.0   182684.0   182409.0   181685.0   181500.0   180861.0   180260.0   179867.0   179891.0    180381.0    180869.0    181603.0   182117.0   183221.0   
3      97565        94       94110        Zip        CA    CA        San Francisco   San Francisco-Oakland-Hayward  San Francisco County   285314.0   283786.0   282878.0   281548.0   280920.0   280286.0   279710.0   280674.0   282418.0    284123.0    285102.0    286893.0   289953.0   294092.0   
4      97743       231       94536        Zip        CA    CA              Fremont   San Francisco-Oakland-Hayward        Alameda County   202048.0   201616.0   201610.0   201552.0   201948.0   202098.0   202230.0   202532.0   203269.0    204486.0    205632.0    206850.0   207674.0   209021.0   
5      97991       274       95123        Zip        CA    CA             San Jose  San Jose-Sunnyvale-Santa Clara    Santa Clara County   199719.0   199149.0   198988.0   198670.0   198752.0   198886.0   199087.0   199671.0   200411.0    201601.0    203071.0    204881.0   207015.0   209344.0   
6      97940       306       95035        Zip        CA    CA             Milpitas  San Jose-Sunnyvale-Santa Clara    Santa Clara County   230694.0   229825.0   229360.0   228470.0   228023.0   227867.0   227836.0   228248.0   228681.0    229585.0    230800.0    232379.0   234362.0   236578.0   
7      97751       314       94544        Zip        CA    CA              Hayward   San Francisco-Oakland-Hayward        Alameda County   158629.0   157990.0   157912.0   157731.0   157981.0   157972.0   157861.0   157898.0   158129.0    158540.0    158884.0    159282.0   159320.0   159750.0   
8      97774       339       94568        Zip        CA    CA               Dublin   San Francisco-Oakland-Hayward        Alameda County   245815.0   245176.0   245075.0   244804.0   244939.0   244838.0   244663.0   244697.0   244929.0    245913.0    246829.0    247861.0   248128.0   248880.0   
9      97952       341       95051        Zip        CA    CA          Santa Clara  San Jose-Sunnyvale-Santa Clara    Santa Clara County   271915.0   270949.0   270675.0   270097.0   269969.0   269915.0   269804.0   270240.0   270631.0    271844.0    273634.0    275955.0   278781.0   281981.0   
10     97717       375       94509        Zip        CA    CA              Antioch   San Francisco-Oakland-Hayward   Contra Costa County    83813.0    83358.0    83263.0    83014.0    82972.0    82792.0    82596.0    82586.0    82727.0     82874.0     83066.0     83296.0    83486.0    83821.0   
11     97576       391       94122        Zip        CA    CA        San Francisco   San Francisco-Oakland-Hayward  San Francisco County   298437.0   297660.0   297334.0   296636.0   296077.0   295662.0   295043.0   295505.0   296165.0    297934.0    299835.0    302114.0   304649.0   307272.0   
12     97748       442       94541        Zip        CA    CA              Hayward   San Francisco-Oakland-Hayward        Alameda County   1740

In [8]:
# Concat the two _dfs

In [11]:
# Using the Pandas `concat` function, join the 
# sfzhvi_df and the sfzhvf_df DataFrames.
# The axis of the concatenation is "columns".
all_zata_df = pd.concat(
    [sfzhvi_df, sfzhvf_df], 
    axis="columns",
    sort=False
)

# Review the resulting DataFrame
display(all_zata_df.head())
display(all_zata_df.tail())


RegionID  SizeRank  RegionName RegionType StateName State           City                          Metro            CountyName  1/31/1996  2/29/1996  3/31/1996  4/30/1996  5/31/1996  6/30/1996  7/31/1996  8/31/1996  9/30/1996  10/31/1996  11/30/1996  12/31/1996  1/31/1997  2/28/1997  3/31/1997  \
0     97564        13       94109        Zip        CA    CA  San Francisco  San Francisco-Oakland-Hayward  San Francisco County   333727.0   332205.0   331788.0   330713.0   330535.0   330277.0   330447.0   331116.0   332377.0    333532.0    335011.0    336512.0   339376.0   342975.0   346418.0   
1     97771        40       94565        Zip        CA    CA      Pittsburg  San Francisco-Oakland-Hayward   Contra Costa County        NaN        NaN        NaN        NaN        NaN        NaN        NaN        NaN        NaN         NaN         NaN         NaN        NaN        NaN        NaN   
2     97711        88       94501        Zip        CA    CA        Alameda  San Francisco-Oakland-Hayward        Alameda County   183651.0   182684.0   182409.0   181685.0   181500.0   180861.0   180260.0   179867.0   179891.0    180381.0    180869.0    181603.0   182117.0   183221.0   184084.0   
3     97565        94       94110        Zip        CA    CA  San Francisco  San Francisco-Oakland-Hayward  San Francisco County   285314.0   283786.0   282878.0   281548.0   280920.0   280286.0   279710.0   280674.0   282418.0    284123.0    285102.0    286893.0   289953.0   294092.0   298403.0   
4     97743       231       94536        Zip        CA    CA        Fremont  San Francisco-Oakland-Hayward        Alameda County   202048.0   201616.0   201610.0   201552.0   201948.0   202098.0   202230.0   202532.0   203269.0    204486.0    205632.0    206850.0   207674.0   209021.0   210463.0   

   4/30/1997  5/31/1997  6/30/1997  7/31/1997  8/31/1997  9/30/1997  10/31/1997  11/30/1997  12/31/1997  1/31/1998  2/28/1998  3/31/1998  4/30/1998  5/31/1998  6/30/1998  7/31/1998  8/31/1998  9/30/1998  10/31/1998  11/30/1998  12/31/1998  1/31/1999  2/28/1999  3/31/1999  4/30/1999  5/31/1999  \
0   348469.0   350581.0   353185.0   356616.0   359395.0   362175.0    365550.0    369570.0    373932.0   377605.0   381445.0   385005.0   390859.0   396038.0   402078.0   406876.0   412903.0   418859.0    425274.0    430373.0    435565.0   439285.0   444493.0   450457.0   456948.0   462748.0   
1        NaN        NaN        NaN        NaN        NaN        NaN         NaN         NaN         NaN        NaN        NaN        NaN        NaN        NaN        NaN        NaN        NaN        NaN         NaN         NaN         NaN        NaN        NaN        NaN        NaN        NaN   
2   185208.0   186371.0   188182.0   190231.0   191937.0   193523.0    194827.0    196532.0    198604.0   200803.0   203159.0   205404.0   207849.0   209557.0   211446.0   213792.0   216449.0   219187.0    220730.0    222557.0    223289.0   225204.0   226706.0   228560.0   229452.0   230340.0   
3   302279.0   306041.0   309712.0   313668.0   316504.0   319517.0    323270.0    327899.0    331859.0   334444.0   337006.0   339813.0   343126.0   346923.0   352197.0   358320.0   363431.0   367884.0    372102.0    378247.0    384261.0   390395.0   396514.0   401997.0   406825.0   410434.0   
4   212374.0   214320.0   216392.0   218944.0   221448.0   223943.0    225919.0    228266.0    231030.0   234016.0   236742.0   239232.0   241606.0   243569.0   246160.0   249127.0   251850.0   254244.0    255610.0    257344.0    258337.0   260688.0   263331.0   265926.0   267636.0   268500.0   

   6/30/1999  7/31/1999  8/31/1999  9/30/1999  10/31/1999  11/30/1999  12/31/1999  1/31/2000  2/29/2000  3/31/2000  4/30/2000  5/31/2000  6/30/2000  7/31/2000  8/31/2000  9/30/2000  10/31/2000  11/30/2000  12/31/2000  1/31/2001  2/28/2001  3/31/2001  4/30/2001  5/31/2001  6/30/2001  7/31/2001  \
0   468232.0   473611.0   478952.0   483869.0    489350.0    496498.0    505059.0   514358.0   522934.0   532303.0   54248

RegionID  SizeRank  RegionName RegionType StateName State                 City                           Metro           CountyName  1/31/1996  2/29/1996  3/31/1996  4/30/1996  5/31/1996  6/30/1996  7/31/1996  8/31/1996  9/30/1996  10/31/1996  11/30/1996  12/31/1996  1/31/1997  2/28/1997  \
221     97544     30373       94074        Zip        CA    CA         San Gregorio   San Francisco-Oakland-Hayward     San Mateo County        NaN        NaN        NaN        NaN        NaN        NaN        NaN        NaN        NaN         NaN         NaN         NaN        NaN        NaN   
222     97775     30742       94569        Zip        CA    CA           Port Costa   San Francisco-Oakland-Hayward  Contra Costa County        NaN        NaN        NaN        NaN        NaN        NaN        NaN        NaN        NaN         NaN         NaN         NaN        NaN        NaN   
223     97512     31457       94021        Zip        CA    CA            Pescadero   San Francisco-Oakland-Hayward     San Mateo County        NaN        NaN        NaN        NaN        NaN        NaN        NaN        NaN        NaN         NaN         NaN         NaN        NaN        NaN   
224     97888     32844       94950        Zip        CA    CA  Point Reyes Station   San Francisco-Oakland-Hayward         Marin County        NaN        NaN        NaN        NaN        NaN        NaN        NaN        NaN        NaN         NaN         NaN         NaN        NaN        NaN   
225     98009     34027       95141        Zip        CA    CA             San Jose  San Jose-Sunnyvale-Santa Clara   Santa Clara County   731728.0   727459.0   722102.0   713873.0   703637.0   693762.0   682234.0   675050.0   672525.0    675308.0    681307.0    687827.0   697401.0   702369.0   

     3/31/1997  4/30/1997  5/31/1997  6/30/1997  7/31/1997  8/31/1997  9/30/1997  10/31/1997  11/30/1997  12/31/1997  1/31/1998  2/28/1998  3/31/1998  4/30/1998  5/31/1998  6/30/1998  7/31/1998  8/31/1998  9/30/1998  10/31/1998  11/30/1998  12/31/1998  1/31/1999  2/28/1999  3/31/1999  4/30/1999  \
221        NaN        NaN        NaN        NaN        NaN        NaN        NaN         NaN         NaN         NaN        NaN        NaN        NaN        NaN        NaN        NaN        NaN        NaN        NaN         NaN         NaN         NaN        NaN        NaN        NaN        NaN   
222        NaN        NaN        NaN        NaN        NaN        NaN        NaN         NaN         NaN         NaN        NaN        NaN        NaN        NaN        NaN        NaN        NaN        NaN        NaN         NaN         NaN         NaN        NaN        NaN        NaN        NaN   
223        NaN        NaN        NaN        NaN        NaN        NaN        NaN         NaN         NaN         NaN        NaN        NaN        NaN        NaN        NaN        NaN        NaN        NaN        NaN         NaN         NaN         NaN        NaN        NaN        NaN        NaN   
224        NaN        NaN        NaN        NaN        NaN        NaN        NaN         NaN         NaN         NaN        NaN        NaN        NaN        NaN        NaN        NaN        NaN        NaN        NaN         NaN         NaN         NaN        NaN        NaN        NaN        NaN   
225   710282.0   709393.0   714836.0   721325.0   734714.0   743163.0   742462.0    734322.0    721232.0    708629.0   695678.0   689736.0   685012.0   691181.0   696799.0   701020.0   699768.0   698512.0   705110.0    713941.0    726706.0    739407.0   748249.0   757827.0   758684.0   757099.0   

     5/31/1999  6/30/1999  7/31/1999  8/31/1999  9/30/1999  10/31/1999  11/30/1999  12/31/1999  1/31/2000  2/29/2000  3/31/2000  4/30/2000  5/31/2000  6/30/2000  7/31/2000  8/31/2000  9/30/2000  10/31/2000  11/30/2000  12/31/2000  1/31/2001  2/28/2001  3/31/2001  4/30/2001  5/31/2001  6/30/2001  \
221        NaN        NaN        NaN        NaN        NaN         NaN         NaN         NaN        NaN        NaN        NaN 

In [34]:
# Group the zips by city then create a new dataframe of the mean values
zata_by_city = (
    all_zata_df
    .drop(columns=['RegionID','SizeRank','RegionName','StateName','State','RegionName'])
    .groupby(['City'])
    .mean()
    .transpose
)

# Review the resulting DataFrame
zata_by_city

<bound method DataFrame.transpose of                          1/31/1996      2/29/1996      3/31/1996      4/30/1996      5/31/1996      6/30/1996      7/31/1996      8/31/1996      9/30/1996     10/31/1996     11/30/1996     12/31/1996      1/31/1997      2/28/1997      3/31/1997      4/30/1997     5/31/1997     6/30/1997  \
City                                                                                                                                                                                                                                                                                              
Alameda              205976.500000  205057.000000  204658.500000  203799.000000  203365.000000  202690.500000  202019.500000  201599.500000  201412.000000  201588.000000  201690.000000  202066.000000  202267.500000  202996.000000  203663.500000  204585.500000  2.056725e+05  2.070395e+05   
Alamo                519268.000000  515543.000000  512075.000000  504934.000000  495856.00

In [32]:

zata_by_city_df = pd.DataFrame()

zata_by_city_df["YoY_Growth_Actual"] = zata_by_city_df["close"].pct_change()




zata_by_city_df

Empty DataFrame
Columns: []
Index: []